# 멋진 작사가 만들기

## 데이터 읽어오기

In [22]:
import glob
import os
import os, re 
import numpy as np
import tensorflow as tf

txt_file_path = os.getenv('HOME')+'/aiffel/lyricist/data/lyrics/*'

txt_list = glob.glob(txt_file_path)

raw_corpus = []

#여러개 텍스트 파일 읽어서 raw_corpus에 저장
for txt_file in txt_list:
    with open(txt_file, "r") as f:
        raw = f.read().splitlines()
        raw_corpus.extend(raw)

print("데이터 크기:", len(raw_corpus))

데이터 크기: 187088


In [23]:
print("Examples:\n", raw_corpus)

Examples:
 ['At first I was afraid', 'I was petrified', 'I kept thinking I could never live without you', 'By my side But then I spent so many nights', "Just thinking how you've done me wrong", 'I grew strong', "I learned how to get along And so you're back", 'From outer space', 'I just walked in to find you', 'Here without that look upon your face I should have changed that fucking lock', 'I would have made you leave your key', 'If I had known for just one second', "You'd be back to bother me Well now go,", 'Walk out the door', 'Just turn around', "Now, you're not welcome anymore Weren't you the one", 'Who tried to break me with desire?', "Did you think I'd crumble?", "Did you think I'd lay down and die? Oh not I,", 'I will survive', 'Yeah', "As Long as I know how to love, I know I'll be alive", "I've got all my life to live", "I've got all my love to give", 'I will survive, I will survive', 'Yeah, yeah', 'It took all the strength I had', "Just not to fall apart I'm trying hard to men

## 데이터 전처리

In [24]:
#정규식을 이용한 문장 정제
def preprocess_sentence(sentence):
    sentence = sentence.lower().strip() 
    sentence = re.sub(r"([?.!,¿])", r" \1 ", sentence) 
    sentence = re.sub(r'[" "]+', " ", sentence) 
    sentence = re.sub(r"[^a-zA-Z?.!,¿]+", " ", sentence) 
    sentence = sentence.strip() 
    sentence = '<start> ' + sentence + ' <end>'
    return sentence

In [25]:
#정제된 문장을 넣을 빈 리스트
corpus = []

for sentence in raw_corpus:
    #길이가 0이거나 단어가 15개가 넘는 문장은 건너뜀
    if len(sentence) == 0 or len(sentence) > 15 : continue
    #공백만 있는 문장은 건너뜀
    if preprocess_sentence(sentence) == '<start>  <end>': continue
    
    #정제 후 담기
    preprocessed_sentence = preprocess_sentence(sentence)
    corpus.append(preprocessed_sentence)
    
print(len(corpus))
print(corpus)

14100
['<start> i was petrified <end>', '<start> i grew strong <end>', '<start> i will survive <end>', '<start> yeah <end>', '<start> yeah , yeah <end>', '<start> and you see me <end>', '<start> well now go , <end>', '<start> oh not i , <end>', '<start> i will survive , <end>', '<start> i will survive <end>', '<start> yeah , yeah <end>', '<start> up <end>', '<start> shut the fuck <end>', '<start> shut the fuck <end>', '<start> up <end>', '<start> shut the fuck <end>', '<start> shut the fuck <end>', '<start> yow , yow , yow <end>', '<start> all right , okay <end>', '<start> i don t wanna <end>', '<start> shut the fuck <end>', '<start> shut the fuck <end>', '<start> i don t wanna <end>', '<start> shut the fuck <end>', '<start> yeah , ho , yow <end>', '<start> shut the fuck <end>', '<start> i was petrified <end>', '<start> i grew strong <end>', '<start> i will survive <end>', '<start> yeah <end>', '<start> yeah , yeah <end>', '<start> and you see me <end>', '<start> well now go , <end>', 

In [26]:
#corpus를 tensor로 변환
def tokenize(corpus):

    tokenizer = tf.keras.preprocessing.text.Tokenizer(
        num_words=12000, 
        filters=' ',
        oov_token="<unk>"
    )
    
    #corpus를 이용해 tokenizer 내부의 단어장 완성
    tokenizer.fit_on_texts(corpus)
    
    #준비한 tokenizer를 이용해 corpus를 Tensor로 변환
    tensor = tokenizer.texts_to_sequences(corpus)   
    
    #입력 데이터의 시퀀스 길이를 일정하게 맞춤
    #만약 시퀀스가 짧다면 문장 뒤에 패딩을 붙여 길이를 맞춤
    tensor = tf.keras.preprocessing.sequence.pad_sequences(tensor, padding='post', maxlen = 15)  
    #문장 앞에 패딩을 붙여 길이를 맞추고 싶다면 padding='pre'를 사용
    
    print(tensor,tokenizer)
    return tensor, tokenizer

tensor, tokenizer = tokenize(corpus)

[[   2    4   98 ...    0    0    0]
 [   2    4 1080 ...    0    0    0]
 [   2    4  111 ...    0    0    0]
 ...
 [   2    4   22 ...    0    0    0]
 [   2    4   22 ...    0    0    0]
 [   2    4   22 ...    0    0    0]] <keras_preprocessing.text.Tokenizer object at 0x7f7d06067ad0>


In [27]:
#단어사전
for idx in tokenizer.index_word:
    print(idx, ":", tokenizer.index_word[idx])

    if idx >= 15: break

1 : <unk>
2 : <start>
3 : <end>
4 : i
5 : ,
6 : .
7 : you
8 : oh
9 : it
10 : me
11 : !
12 : a
13 : the
14 : yeah
15 : my


In [28]:
#소스 문장, 타겟 문장 생성

#tensor에서 마지막 토큰을 잘라내서 소스 문장을 생성
#마지막 토큰은 <end>가 아니라 <pad>일 가능성이 높음
src_input = tensor[:, :-1]  

#tensor에서 <start>를 잘라내서 타겟 문장을 생성
tgt_input = tensor[:, 1:]    

print(src_input[0])
print(tgt_input[0])

[   2    4   98 1336    3    0    0    0    0    0    0    0    0    0]
[   4   98 1336    3    0    0    0    0    0    0    0    0    0    0]


In [29]:
print(tensor.shape)
print(src_input.shape)
print(tgt_input.shape)

(14100, 15)
(14100, 14)
(14100, 14)


## 데이터셋 분리

In [30]:
from sklearn.model_selection import train_test_split

#데이터셋을 train, test 데이터로 분리
enc_train, enc_val, dec_train, dec_val = train_test_split(src_input, tgt_input, test_size=0.2)

print("Source Train:", enc_train.shape)
print("Target Train:", dec_train.shape)

Source Train: (11280, 14)
Target Train: (11280, 14)


## 모델 형성

In [31]:
lib_size = tokenizer.num_words
embedding_size = 256
hidden_size = 1024

model = tf.keras.Sequential()
model.add(tf.keras.layers.Embedding(lib_size, embedding_size))
model.add(tf.keras.layers.LSTM(hidden_size, return_sequences=True))
model.add(tf.keras.layers.LSTM(hidden_size, return_sequences=True))
model.add(tf.keras.layers.Dense(lib_size))

model.summary()

Model: "sequential"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
embedding (Embedding)        (None, None, 256)         3072000   
_________________________________________________________________
lstm (LSTM)                  (None, None, 1024)        5246976   
_________________________________________________________________
lstm_1 (LSTM)                (None, None, 1024)        8392704   
_________________________________________________________________
dense (Dense)                (None, None, 12000)       12300000  
Total params: 29,011,680
Trainable params: 29,011,680
Non-trainable params: 0
_________________________________________________________________


## 모델 훈련

In [32]:
optimizer = tf.keras.optimizers.Adam()
loss = tf.keras.losses.SparseCategoricalCrossentropy(
    from_logits=True,
    reduction='none'
)

model.compile(loss=loss, optimizer=optimizer)
model.fit(enc_train, dec_train, epochs=10)

Epoch 1/10
353/353 [==============================] - 29s 73ms/step - loss: 2.1741
Epoch 2/10
353/353 [==============================] - 26s 74ms/step - loss: 1.1859
Epoch 3/10
353/353 [==============================] - 26s 74ms/step - loss: 1.1216
Epoch 4/10
353/353 [==============================] - 26s 74ms/step - loss: 1.0399
Epoch 5/10
353/353 [==============================] - 26s 75ms/step - loss: 0.9827
Epoch 6/10
353/353 [==============================] - 27s 75ms/step - loss: 0.9251
Epoch 7/10
353/353 [==============================] - 27s 75ms/step - loss: 0.8796
Epoch 8/10
353/353 [==============================] - 27s 75ms/step - loss: 0.8366
Epoch 9/10
353/353 [==============================] - 27s 76ms/step - loss: 0.7948
Epoch 10/10
353/353 [==============================] - 27s 75ms/step - loss: 0.7665


## 모델 평가

In [33]:
#모델에게 시작 문장을 전달하면 모델이 시작 문장을 바탕으로 작문을 진행
def generate_text(model, tokenizer, init_sentence="<start>", max_len=20):
    #테스트를 위해서 입력받은 init_sentence도 일단 텐서로 변환
    test_input = tokenizer.texts_to_sequences([init_sentence])
    test_tensor = tf.convert_to_tensor(test_input, dtype=tf.int64)
    end_token = tokenizer.word_index["<end>"]

    #루프를 돌면서 단어 하나씩 생성
    while True:
        #입력받은 문장의 텐서를 입력
        predict = model(test_tensor)  
        #예측된 값 중 가장 높은 확률인 word index를 뽑음
        predict_word = tf.argmax(tf.nn.softmax(predict, axis=-1), axis=-1)[:, -1]  

        #위에서 예측된 word index를 문장 뒤에 붙임 
        test_tensor = tf.concat([test_tensor, tf.expand_dims(predict_word, axis=0)], axis=-1)
        
        #모델이 <end>를 예측했거나, max_len에 도달했다면 문장 생성을 마침
        if predict_word.numpy()[0] == end_token: break
        if test_tensor.shape[1] >= max_len: break

    generated = ""
    #tokenizer를 이용해 word index를 단어로 하나씩 변환
    for word_index in test_tensor[0].numpy():
        generated += tokenizer.index_word[word_index] + " "

    return generated 

In [34]:
generate_text(model, tokenizer, init_sentence="<start> i love", max_len=20)

'<start> i love you <end> '

In [35]:
generate_text(model, tokenizer, init_sentence="<start> i am", max_len=20)

'<start> i am a god <end> '

In [36]:
generate_text(model, tokenizer, init_sentence="<start> you are", max_len=20)

'<start> you are me <end> '

In [37]:
generate_text(model, tokenizer, init_sentence="<start> we are", max_len=20)

'<start> we are stardust <end> '

In [38]:
generate_text(model, tokenizer, init_sentence="<start> he is", max_len=20)

'<start> he is me <end> '

In [39]:
generate_text(model, tokenizer, init_sentence="<start> she is", max_len=20)

'<start> she is a bitch <end> '

In [40]:
generate_text(model, tokenizer, init_sentence="<start> he was", max_len=20)

'<start> he was a monster <end> '

In [41]:
generate_text(model, tokenizer, init_sentence="<start> she was", max_len=20)

'<start> she was confident <end> '

In [42]:
generate_text(model, tokenizer, init_sentence="<start> we were", max_len=20)

'<start> we were stop <end> '

In [43]:
generate_text(model, tokenizer, init_sentence="<start> happy", max_len=20)

'<start> happy york <end> '

In [44]:
generate_text(model, tokenizer, init_sentence="<start> terrible", max_len=20)

'<start> <unk> and frog <end> '

-----

# 정리

## maxlen = 15
- 데이터 전처리 과정에서 너무 긴 문장은 노래 가사 작사하기에 어울리지 않을 수 있기 때문에 문장을 토큰화 했을 때 토큰의 개수가 15개를 넘어가지 않도록 했다.
- 때문에 padding 시 maxlen 역시 15로 지정했다.

## 모델 훈련 결과
- epoch 10에서 loss: 0.7665로 꽤 낮은 loss가 나왔다.
- 모델 평가 시 노드에서 제공한 예시 말고도 다른 단어를 입력했을 때 매끄럽게 문장을 만들어 냈으며 terrible과 같은 없는 단어는 < unk >로 잘 나타내었다.